# Query the Barb API using python

In this demo we will show you how to query the Barb API using Python. We will do this first without making use of the pybarb package (as you may wish to develop your own software from scratch). We will then show you how to use the pybarb package to make the same query.

Note the full API documentation can be found [here](https://barb-api.co.uk/api-docs). 

It might also be useful to consult the [Getting Started](https://barb-api.co.uk/api-docs#section/Getting-started) section for information about authentication and basic API usage.

## Querying the API without pybarb

First we use the code and instructions from the notebook "Connecting to the BARB API using Python" to connect to the API.

In [1]:
import requests
import json

# Set the working directory
working_directory = '/Users/simon_business/Documents/disposable/clients/BARB/'

# Get the access token
with open(working_directory + "creds.json") as file:
    creds = json.load(file)
api_root = "https://barb-api.co.uk/api/v1/"
token_request_url = api_root + "auth/token/"
response = requests.post(token_request_url, data = creds)
access_token = json.loads(response.text)['access']

# Set the headers
headers = {'Authorization': 'Bearer {}'.format(access_token)}

We now have everything we need to query the BARB API. Let's start by getting the programme ratings for all programmes broadcast on BBC One to the BBC Network panel between 25th and 31st December 2022. 

We use [the endpoint documentation](https://barb-api.co.uk/api-docs#tag/Events/operation/ProgrammeRatings) to understand which query parameters can be used and what values they can take. We set the parameters for the query as follows:

In [27]:
params = {"min_transmission_date": "2022-12-25","max_transmission_date":"2022-12-31", 
          "station_code": 10, 
          "panel_code": 50,
         "consolidated": True, "limit": 5000}

Now we can query the endpoint by passing it the parameters and the headers we just created. We will use the requests library to do this. We will also use the json library to format the response as a JSON object.

In [28]:
api_url = api_root + "programme_ratings/"
r = requests.get(url=api_url, params=params, headers=headers)
api_data = r.json()

The data has a nested structure which is explained in the API documentation. 

In [29]:
api_data

{'events': [{'panel': {'panel_code': 50,
    'panel_region': 'BBC Network',
    'is_macro_region': False},
   'station': {'station_code': 10, 'station_name': 'BBC1'},
   'transmission_log_programme_name': 'SONGS OF PRAISE: CHRISTMAS DAY CAROLS FR',
   'programme_type': 'programme',
   'programme_start_datetime': {'barb_reporting_datetime': '2022-12-25 11:00:33',
    'barb_polling_datetime': '2022-12-25 11:00:33',
    'standard_datetime': '2022-12-25 11:00:33'},
   'programme_duration': 32,
   'spans_normal_day': False,
   'sponsor': {'sponsor_code': None, 'bumpers': 'not_sponsored'},
   'broadcaster_transmission_code': '7502356405812',
   'live_status': 'unknown',
   'uk_premier': True,
   'broadcaster_premier': True,
   'repeat': False,
   'programme_content': {'content_name': 'Songs of Praise: Series 2022',
    'barb_content_id': 7398794,
    'broadcaster_content_id': 'm001gnhz',
    'metabroadcast_information': {'metabroadcast_content_id': 'p9jg8d'},
    'episode': {'episode_number'

This data can be flattened using the json_normalize() function from the pandas library. This function takes a JSON object and flattens it into a pandas DataFrame. 

In [30]:
from pandas import json_normalize
json_normalize(api_data['events']).head()


transmission_log_programme_name programme_type   
0  SONGS OF PRAISE: CHRISTMAS DAY CAROLS FR      programme  \
1        MRS BROWN'S BOYS CHRISTMAS SPECIAL      programme   
2                   FILM: ABOMINABLE (2019)      programme   
3                                   WEATHER      programme   
4                                 Breakfast      programme   

   programme_duration  spans_normal_day broadcaster_transmission_code   
0                  32             False                 7502356405812  \
1                  29             False                14320869134812   
2                  86             False                25914801935812   
3                   2             False                32723490655812   
4                 179             False                23380242589812   

  live_status  uk_premier  broadcaster_premier  repeat   
0     unknown        True                 True   False  \
1     unknown        True                 True   False   
2     unknown       False                False    True   
3     unknown        True                 True   False   
4     unknown        True                 True   False   

                                           platforms  ...   
0  [Analogue Terrestrial, Digital Terrestrial, An...  ...  \
1  [Analogue Terrestrial, Digital Terrestrial, An...  ...   
2  [Analogue Terrestrial, Digital Terrestrial, An...  ...   
3  [Analogue Terrestrial, Digital Terrestrial, An...  ...   
4  [Analogue Terrestrial, Digital Terrestrial, An...  ...   

           programme_content.content_name  programme_content.barb_content_id   
0            Songs of Praise: Series 2022                            7398794  \
1  Mrs Brown's Boys: Series 18, Episode 1                            7398804   
2                 FILM: Abominable (2019)                            6139597   
3                BBC Weather: Series 2022                            7398788   
4                  Breakfast: Series 2022                            7398785   

  programme_content.broadcaster_content_id   
0                                 m001gnhz  \
1                                 m001gnjn   
2                                 m0012vhh   
3                                 m001gnjt   
4                                 m001gnht   

   programme_content.metabroadcast_information.metabroadcast_content_id   
0                                             p9jg8d                     \
1                                             p9jg8w                      
2                                             pjtpd9                      
3                                             p9jg8y                      
4                                             p9jg8b                      

   programme_content.episode.episode_number   
0                                         0  \
1                                         1   
2                                         0   
3                                         0   
4                                         0   

  programme_content.episode.episode_name   
0      Christmas Day Carols from Cardiff  \
1                          Shining Mammy   
2                             Abominable   
3                             25/12/2022   
4                             25/12/2022   

  programme_content.series.series_number   
0                                   2022  \
1                                     18   
2                                 (2019)   
3                                   2022   
4                                   2022   

  programme_content.series.number_of_episodes   
0                                           0  \
1                                           2   
2                                           0   
3                                           0   
4                                           0   

  programme_content.series.broadcaster_series_id programme_content.genre  
0                                           None               Religious  
1                

If the dataset is large then it will be returned over multiple pages. To return all the data we need to loop through the pages and append the data to a list. The following code will return all the data for the last half of 2022.

In [31]:
api_url = api_root + "programme_ratings/"

# The query parameters
params = {"min_transmission_date": "2022-07-01","max_transmission_date":"2022-12-31", 
          "station_code": 10, 
          "panel_code": 50,
         "consolidated": True, "limit": 5000}

# Query the API and turn the response into json
api_data = []
r = requests.get(url=api_url, params=params, headers=headers)
api_data.append(r.json())

while r.headers.__contains__("X-Next"):
    print(f'Downloading the next page from {r.headers["X-Next"]}')
    x_next_url = r.headers["X-Next"]
    r = requests.get(url=x_next_url, headers=headers)
    api_data.append(r.json())


However to properly assemble a table of audience data we need to join the `event` data with the `audience_categories` data. This is straightforward to do using the `merge()` function from the pandas library, however the pybarb package handles all of this for you.

## Querying the API with pybarb

First we connect to the API using the `pybarb` package as described in "Connecting to the Barb API using Python". 

In [2]:
import pybarb as pb

# Create a BarbAPI object and connect
barb_api = pb.BarbAPI(creds)
barb_api.connect()

Now we can use `programme_ratings` method to query the programme ratings endpoint. This method will handle the pagination for us.

In [3]:
bbc_1_progs = barb_api.programme_ratings(min_transmission_date = "2022-12-25", 
                           max_transmission_date = "2022-12-31", 
                           station="BBC1", panel="bbc network", 
                           consolidated=True)

The downloaded data can be viewed in the `api_response_data` attribute.

In [4]:
bbc_1_progs.api_response_data

{'endpoint': 'programme_ratings',
 'events': [{'panel': {'panel_code': 50,
    'panel_region': 'BBC Network',
    'is_macro_region': False},
   'station': {'station_code': 10, 'station_name': 'BBC1'},
   'transmission_log_programme_name': 'SONGS OF PRAISE: CHRISTMAS DAY CAROLS FR',
   'programme_type': 'programme',
   'programme_start_datetime': {'barb_reporting_datetime': '2022-12-25 11:00:33',
    'barb_polling_datetime': '2022-12-25 11:00:33',
    'standard_datetime': '2022-12-25 11:00:33'},
   'programme_duration': 32,
   'spans_normal_day': False,
   'sponsor': {'sponsor_code': None, 'bumpers': 'not_sponsored'},
   'broadcaster_transmission_code': '7502356405812',
   'live_status': 'unknown',
   'uk_premier': True,
   'broadcaster_premier': True,
   'repeat': False,
   'programme_content': {'content_name': 'Songs of Praise: Series 2022',
    'barb_content_id': 7398794,
    'broadcaster_content_id': 'm001gnhz',
    'metabroadcast_information': {'metabroadcast_content_id': 'p9jg8d'}

However it is much more convenient to use the `to_dataframe` method to convert the response to a pandas dataframe. This method will also do things like convert the dates to datetime objects and merge the `event` data with the `audience_categories` data.


In [5]:
bbc_1_progs.to_dataframe()

panel_region station_name                            programme_name   
0      BBC Network         BBC1  Songs Of Praise: Christmas Day Carols Fr  \
1      BBC Network         BBC1  Songs Of Praise: Christmas Day Carols Fr   
2      BBC Network         BBC1  Songs Of Praise: Christmas Day Carols Fr   
3      BBC Network         BBC1  Songs Of Praise: Christmas Day Carols Fr   
4      BBC Network         BBC1  Songs Of Praise: Christmas Day Carols Fr   
...            ...          ...                                       ...   
24816  BBC Network         BBC1                        North West Tonight   
24817  BBC Network         BBC1                        North West Tonight   
24818  BBC Network         BBC1                        North West Tonight   
24819  BBC Network         BBC1                        North West Tonight   
24820  BBC Network         BBC1                        North West Tonight   

      programme_type programme_start_datetime  programme_duration_minutes   
0          programme      2022-12-25 11:00:33                          32  \
1          programme      2022-12-25 11:00:33                          32   
2          programme      2022-12-25 11:00:33                          32   
3          programme      2022-12-25 11:00:33                          32   
4          programme      2022-12-25 11:00:33                          32   
...              ...                      ...                         ...   
24816      programme      2022-12-31 17:35:47                           5   
24817      programme      2022-12-31 17:35:47                           5   
24818      programme      2022-12-31 17:35:47                           5   
24819      programme      2022-12-31 17:35:47                           5   
24820      programme      2022-12-31 17:35:47                           5   

       spans_normal_day  uk_premiere  broadcaster_premiere  programme_repeat   
0                 False         True                  True             False  \
1                 False         True                  True             False   
2                 False         True                  True             False   
3                 False         True                  True             False   
4                 False         True                  True             False   
...                 ...          ...                   ...               ...   
24816             False         True                  True             False   
24817             False         True                  True             False   
24818             False         True                  True             False   
24819             False         True                  True             False   
24820             False         True                  True             False   

      episode_number episode_name genre  audience_size_hundreds   
0               None         None  None                    4480  \
1               None         None  None                    6854   
2               None         None  None                    2685   
3               None         None  None                    4292   
4               None         None  None                     384   
...              ...          ...   ...                     ...   
24816           None         None  None                       0   
24817           None         None  None                     150   
24818           None         None  None                       7   
24819           None         None  None                      15   
24820           None         None  None                       0   

      date_of_transmission                 audience_name   
0               2022-12-25                     All Homes  \
1               2022-12-25                    All Adults   
2               2022-12-25                       All Men   
3               2022-12-25               All Houseperson   
4               2022-12-25        All Children aged 4-15   
...                    ...    